In [1]:
# There, done. That was easy.
# That's all we needed to do, right?
import numpy as np
import pandas as pd
import xgboost as xgb

import json
import re

In [2]:
# Read in data
FIRST = 5 # First year is 2015
LAST = 7 # Last year is 2017

raw_data = [pd.read_csv('data/201%d.csv' % i) for i in xrange(FIRST, LAST + 1)]

years = np.array([np.repeat('201%d' % (i + FIRST,), raw_data[i].shape[0])
                  for i in xrange(0, LAST - FIRST + 1)])

# raw_data eventually combined into columns in data
data = pd.DataFrame({'year': np.hstack(years)})

/anaconda3/envs/py27/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (5,108,121,196,197,198) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [ ]:
# helpers to define how to get columns
number = re.compile('\d+')
def get_first_number(val):
    matched = number.match(str(val))
    if matched:
        return int(matched.group())
    else:
        return np.nan

satisfaction_strs = {
    'I love my job': 10,
    'I\'m somewhat satisfied with my job': 7.5,
    'I\'m neither satisfied nor dissatisfied with my job': 5
    'I\'m somewhat dissatisfied with my job': 2.5,
    'I hate my job': 0,
}

def get_satisfaction(response):
    if type(response) == 'float64':
        return response

    if response in satisfaction_strs:
        return satisfaction_strs[response]

    return np.nan

In [ ]:
# define how to get each column
colnames = [
    {
        'new_name': 'jobSatisfaction',
        'old_names': [
            'Job Satisfaction',
            'job_satisfaction',
            'JobSatisfaction',
        ],
        'apply': np.vectorize(get_satisfaction),
    },
    {
        'new_name': 'experience',
        'old_names': [
            'Years IT / Programming Experience',
            'experience_range',
            'YearsProgram',
        ],
        'apply': np.vectorize(get_first_number),
    },
    {
        'new_name': 'salary',
        'old_names': [
            'Compensation: midpoint',
            'salary_midpoint',
            'Salary'
        ]
    },
]

In [ ]:
# Take previous cell and use information to make the "data" dataframe
def get_col(data, coldata):
    new_col = np.array([dataset[colname]
                        for dataset, colname in zip(data, coldata['old_names'])])
    if 'apply' in coldata:
        new_col = coldata['apply'](new_col)
    return np.hstack(new_col)

new_cols = {row['new_name']: get_col(raw_data, row) for row in colnames}
data = data.assign(**new_cols)

In [ ]:
# Parse languages
langs = ['JavaScript', 'SQL', 'Java', 'C#', 'Python', 'PHP', 'C++', 'C', 
         'TypeScript', 'Ruby', 'Swift', 'Objective-C', 'VB.net', 'Assembly',
         'R', 'Perl', 'VBA', 'Matlab', 'Go', 'Scala', 'Groovy', 'CoffeeScript',
         'Visual Basic', 'Lua', 'Haskell', 'Clojure']

for lang in langs:
    lang_data = []
    col_2015_index = 'Current Lang & Tech: %s' % lang
    if col_2015_index in raw_data[0]:
        lang_data.append(raw_data[0][col_2015_index].notnull().astype('int8').values)
    else:
        lang_data.append(np.repeat(0, raw_data[0].shape[0]))

    lang_data.append(raw_data[1]['tech_do']
                             .fillna('')
                             .map(lambda langs: lang in langs.split('; ')))
    lang_data.append(raw_data[2]['HaveWorkedLanguage']
                             .fillna('')
                             .map(lambda langs: lang in langs.split('; ')))
    data = data.assign(**{lang: np.hstack(lang_data)})

### Placing into entry into region rather than country for easier analysis

In [3]:
data2015 = pd.read_csv('data/2015.csv')
data2016 = pd.read_csv('data/2016.csv')
data2017 = pd.read_csv('data/2017.csv')

/anaconda3/envs/py27/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2718: DtypeWarning: Columns (5,108,121,196,197,198) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [142]:
#These are the common features among each of the data sets
cols = ['Country', 'Gender', 'Experience', 'Occupation', 'Salary', 'Job Satisfaction']

total_data = pd.DataFrame(columns=cols)

total_data_2015 = data2015[(pd.isna(data2015['Country']) == False)]
total_data_2015 = total_data_2015[(pd.isna(total_data_2015['Gender']) == False)]
total_data_2015 = total_data_2015[(pd.isna(total_data_2015['Years IT / Programming Experience']) == False)]
total_data_2015["Experience"] = total_data_2015['Years IT / Programming Experience']
total_data_2015 = total_data_2015[(pd.isna(total_data_2015['Occupation']) == False)]
total_data_2015 = total_data_2015[(pd.isna(total_data_2015['Compensation: midpoint']) == False)]
total_data_2015["Salary"] = total_data_2015['Compensation: midpoint']
total_data_2015 = total_data_2015[(pd.isna(total_data_2015['Job Satisfaction']) == False)]

total_data_2016 = data2016[(pd.isna(data2016['country']) == False)]
total_data_2016["Country"] = total_data_2016['country']
total_data_2016 = total_data_2016[(pd.isna(total_data_2016['gender']) == False)]
total_data_2016["Gender"] = total_data_2016['gender']
total_data_2016 = total_data_2016[(pd.isna(total_data_2016['experience_range']) == False)]
total_data_2016["Experience"] = total_data_2016['experience_range']
total_data_2016 = total_data_2016[(pd.isna(total_data_2016['occupation']) == False)]
total_data_2016["Occupation"] = total_data_2016['occupation']
total_data_2016 = total_data_2016[(pd.isna(total_data_2016['salary_midpoint']) == False)]
total_data_2016["Salary"] = total_data_2016['salary_midpoint']
total_data_2016 = total_data_2016[(pd.isna(total_data_2016['job_satisfaction']) == False)]
total_data_2016["Job Satisfaction"] = total_data_2016['job_satisfaction']

total_data_2017 = data2017[(pd.isna(data2017['Country']) == False)]
total_data_2017 = total_data_2017[(pd.isna(total_data_2017['Gender']) == False)]
total_data_2017 = total_data_2017[(pd.isna(total_data_2017['YearsProgram']) == False)]
total_data_2017["Experience"] = total_data_2017['YearsProgram']
total_data_2017 = total_data_2017[(pd.isna(total_data_2017['DeveloperType']) == False)]
total_data_2017["Occupation"] = total_data_2017['DeveloperType']
total_data_2017 = total_data_2017[(pd.isna(total_data_2017['Salary']) == False)]
total_data_2017 = total_data_2017[(pd.isna(total_data_2017['JobSatisfaction']) == False)]
total_data_2017["Job Satisfaction"] = total_data_2017['JobSatisfaction']

total_data = pd.concat([total_data_2015[["Country", "Gender", 'Experience', 'Occupation', 'Salary', 'Job Satisfaction']], total_data], axis=0)
total_data = pd.concat([total_data_2016[["Country", "Gender", 'Experience', 'Occupation', 'Salary', 'Job Satisfaction']], total_data], axis=0)
total_data = pd.concat([total_data_2017[["Country", "Gender", 'Experience', 'Occupation', 'Salary', 'Job Satisfaction']], total_data], axis=0)
# len(total_data)

total_data.head()
total_data.to_csv()

/anaconda3/envs/py27/lib/python2.7/site-packages/ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()


',Country,Gender,Experience,Occupation,Salary,Job Satisfaction\n2,United Kingdom,Male,20 or more years,Other,113750.0,9.0\n14,United Kingdom,Male,20 or more years,Embedded applications/devices developer,100000.0,8.0\n17,United States,Male,20 or more years,Web developer; Embedded applications/devices developer; DevOps specialist; Quality assurance engineer; Other,130000.0,8.0\n22,Israel,Male,10 to 11 years,Other,100764.0,9.0\n25,United States,Male,20 or more years,Web developer,175000.0,7.0\n34,Croatia,Male,7 to 8 years,Embedded applications/devices developer,14838.7096774194,8.0\n36,Argentina,Male,20 or more years,Web developer; Mobile developer; Desktop applications developer,28200.0,9.0\n52,Brazil,Male,4 to 5 years,Web developer; Mobile developer; Quality assurance engineer,15674.203821656101,5.0\n54,Germany,Male,8 to 9 years,Web developer,64516.1290322581,9.0\n57,Italy,Male,11 to 12 years,Mobile developer,43010.752688172004,6.0\n61,India,Male,3 to 4 years,Web developer,6636.32359418

In [141]:
total_data["Job Satisfaction"].unique()

array([9.0, 8.0, 7.0, 5.0, 6.0, 2.0, 10.0, 4.0, 3.0, 1.0, 0.0,
       'I love my job', "I don't have a job",
       "I'm somewhat satisfied with my job",
       "I'm somewhat dissatisfied with my job",
       "I'm neither satisfied nor dissatisfied", 'Other (please specify)',
       'I hate my job',
       "I'm neither satisfied nor dissatisfied with my job"], dtype=object)

In [135]:
#This code is in progress: places country into region
reg_dict = {}
countries = data2016.groupby("un_subregion")["country"].unique()
u_reg = data2016["un_subregion"].unique()
u_reg = np.delete(u_reg, 16) #delete nan
u_reg = sorted(u_reg, key=str.lower)

for i in range(len(u_reg)-1):
    country_list = countries[i]
    for country in country_list:
        reg_dict[country] = u_reg[i]

nans = []
total_data = data2016[(pd.isna(data2016["country"]) == False)].drop(columns=["Unnamed: 0"])
# print(total_data[""])
df = data2016.dropna(thresh=9)
# print(df)